In [2]:
# Dependencies
import sys
import datetime as dt
from pprint import pprint
import pandas as pd
from library.authorize.config import api_id, api_key
from library.authorize.api import UnleashedApi

In [3]:
def file_input():
    file_import = True
    while file_import:
        # User input to get excel file name
        global excel_file_name
        excel_file_name = input("Please enter in the excel file name: ")

        # Enter to exit program
        exit_strat = ["quit", "cancel", "exit"]
        if excel_file_name in exit_strat:
            sys.exit(1)

        # Excel file path
        excel_path = f"product_list_import/{excel_file_name}.xlsx"

        try:
            # Read excel file as df
            # Keep blank rows for easy copy and paste
            global product_df
            product_df = pd.read_excel(excel_path, skip_blank_lines=False)

            # Stop file_import loop
            file_import = False

        except FileNotFoundError:
            print("Sorry, there is no such file in directory. Please try again.\n")

    # Run pick_enquiry function to choose which enquiry to run
    # pick_enquiry()

    return excel_file_name, product_df

In [4]:
file_input()

Please enter in the excel file name: test


('test',
   Product Code                                  Description  Quantity On Hand
 0       PPPRAS               Partial Bulk Pro Accelerator S               NaN
 1   BXPCPRTRKT  Box ProCell Pro Aftercare Serums Sample Set            5392.0
 2  BXPCPRMN2ML   Box ProCell Pro Microneedling Solution 2ml            1450.0
 3   INPULLULAN                          Ingredient Pullulan               0.0)

In [5]:
def export_to_excel(dataframe):
    # Grab datetime
    today = dt.datetime.now().strftime(format="%Y%m%d")

    try:
        # Save as csv
        dataframe.to_excel(f"unl_enquiry/{today}_unl_{excel_file_name}.xlsx", index=False)
    except PermissionError:
        print("Oh no. You have the file already open! Close it and try again.")
    except:
        raise

    # Print to console
    print("\nCompleted! Here are the top few rows:")
    print("-" * 40)
    print(dataframe.head().to_string(index=False))
    print("-" * 40 + "\n")

In [6]:
def get_po_response():
    # Unleashed api base url
    api_url = "https://api.unleashedsoftware.com"

    # Authorize and connect to api
    auth = UnleashedApi(api_url, api_id, api_key)

    # Get response
    purchase_orders = auth.get_request(method="PurchaseOrders?").json()

    return purchase_orders

In [20]:
def get_purchases(product_df):

    # Run get_des_response function
    print("\nGrabbing order quantities on purchase...")

    # Unleashed api base url
    api_url = "https://api.unleashedsoftware.com"

    # Authorize and connect to api
    auth = UnleashedApi(api_url, api_id, api_key)
    
    # Create dictionary to hold order quantities for each product
    order_quantity_dict = {}

    # Append each product in product_df to order_quantity_dict as dictionaries
    for product in product_df["Product Code"]:
        # Add product as key with the value as a list
        order_quantity_dict[product] = []    
    
    # print(order_quantity_dict)
    
    # Keep track of number of items
    item_count = 0
    
    # Paginate through arbitrary large number
    for x in range(100):

        # Get response
        purchase_orders = auth.get_request(method=f"PurchaseOrders/{x+1}?").json()
        
        # Add number of orders to item count
        item_count += len(purchase_orders["Items"])
        
        # print("Length of page: {}".format(len(purchase_orders["Items"])))
        # print(f"Total item count: {item_count}")
        
        for product, order_quantity_list in order_quantity_dict.items():
            
            for order in purchase_orders["Items"]:
            
                if order["OrderStatus"] != "Complete":                
                    
                    for line in order["PurchaseOrderLines"]:
                        
                        if line["Product"]["ProductCode"] == product:
                            
                            # Append order quantity to list in order quantity dictionary
                            order_quantity_list.append(line["OrderQuantity"])
            
        # Break loop if item_count hits max number of orders
        if item_count == purchase_orders["Pagination"]["NumberOfItems"]:
            break
    
    # print(order_quantity_dict)
    
    # Add new blank column
    product_df["Quantity On Purchase"] = ""
    
    for i, product in enumerate(product_df["Product Code"]):
        
        for key, order_quantity_list in order_quantity_dict.items():
            
            if product == key:
                
                # Insert quantity at index
                product_df.at[product_df.index[i], "Quantity On Purchase"] = sum(order_quantity_list)
        
    # Reorder columns
    product_df = product_df[["Product Code", "Description", "Quantity On Hand", "Quantity On Purchase"]]

    # Run export_to_excel function to grab final file
    # export_to_excel(product_df)

    # Return product_df
    return product_df

In [21]:
get_purchases(product_df)


Grabbing order quantities on purchase...


Product Code                                  Description  Quantity On Hand  \
0       PPPRAS               Partial Bulk Pro Accelerator S               NaN   
1   BXPCPRTRKT  Box ProCell Pro Aftercare Serums Sample Set            5392.0   
2  BXPCPRMN2ML   Box ProCell Pro Microneedling Solution 2ml            1450.0   
3   INPULLULAN                          Ingredient Pullulan               0.0   

  Quantity On Purchase  
0                  111  
1                 2500  
2                 2500  
3                  100

In [114]:
def test():
    # Unleashed api base url
    api_url = "https://api.unleashedsoftware.com"

    # Authorize and connect to api
    auth = UnleashedApi(api_url, api_id, api_key)
    
    # Add new blank column
    product_df["Quantity On Purchase"] = ""
    
    # Instantiate total order quantity count for each item
    total_order_quantity = 0
    
    for x in range(3):
    
        # Get response
        purchase_orders = auth.get_request(method=f"PurchaseOrders/{x+1}?").json()
        
        for order in purchase_orders["Items"]:
            
            if order["OrderStatus"] != "Complete":                
                    
                for line in order["PurchaseOrderLines"]:
                        
                    for i, product in enumerate(product_df["Product Code"]):
                        
                        if line["Product"]["ProductCode"] == product:
                            
                            # Add order quantity to total
                            total_order_quantity += line["OrderQuantity"]
                            
                            print(line["OrderQuantity"])
                        
                            # Insert quantity at index
                            product_df.at[product_df.index[i], "Quantity On Purchase"] = total_order_quantity
                            
                            # Reset total_order_quantity
                            total_order_quantity = 0
    
    return product_df

In [115]:
test()

2500.0
2500.0
100.0
11.0
100.0


Product Code                                  Description  Quantity On Hand  \
0       PPPRAS               Partial Bulk Pro Accelerator S               NaN   
1   BXPCPRTRKT  Box ProCell Pro Aftercare Serums Sample Set            5392.0   
2  BXPCPRMN2ML   Box ProCell Pro Microneedling Solution 2ml            1450.0   
3   INPULLULAN                          Ingredient Pullulan               0.0   

  Quantity On Purchase  
0                  100  
1                 2500  
2                 2500  
3                  100

In [15]:
# def get_bom_response():
# Unleashed api base url
api_url = "https://api.unleashedsoftware.com"

# Authorize and connect to api
auth = UnleashedApi(api_url, api_id, api_key)

# Keep track of number of items
item_count = 0

for x in range(4):
    
    # Get response
    purchase_orders = auth.get_request(method=f"PurchaseOrders/{x+1}?").json()
    
    # Add number of orders to item count
    item_count += len(purchase_orders["Items"])
    
    print("Length of page: {}".format(len(purchase_orders["Items"])))
    print(f"Total item count: {item_count}")
    
    if item_count == purchase_orders["Pagination"]["NumberOfItems"]:
        break
    

Length of page: 200
Total item count: 200
Length of page: 200
Total item count: 400
Length of page: 158
Total item count: 558


In [87]:
pprint(purchase_orders)

{'Items': [{'BCSubTotal': 696.0,
            'BCTaxTotal': 0.0,
            'BCTotal': 696.0,
            'Comments': None,
            'CompletedDate': None,
            'CreatedBy': 'connor@cellese.com',
            'CreatedOn': '/Date(1440616172096)/',
            'Currency': {'CurrencyCode': 'USD',
                         'Description': 'United States of America, Dollars',
                         'Guid': 'e9718993-b8d1-4084-9476-5b0153413223',
                         'LastModifiedOn': '/Date(1423681841700)/'},
            'DeliveryCity': 'Irvine',
            'DeliveryCountry': 'United State of Amercia',
            'DeliveryName': '17971 Sky Park Circle, Suite G',
            'DeliveryPostCode': '92614',
            'DeliveryRegion': 'CA',
            'DeliveryStreetAddress': '17971 Sky Park Circle, Suite G',
            'DeliveryStreetAddress2': None,
            'DeliverySuburb': None,
            'DiscountRate': 0.0,
            'ExchangeRate': 1.0,
            'Guid': 'f20f

            'BCTaxTotal': 0.0,
            'BCTotal': 250.0,
            'Comments': None,
            'CompletedDate': None,
            'CreatedBy': 'connor@cellese.com',
            'CreatedOn': '/Date(1440797759197)/',
            'Currency': {'CurrencyCode': 'USD',
                         'Description': 'United States of America, Dollars',
                         'Guid': 'e9718993-b8d1-4084-9476-5b0153413223',
                         'LastModifiedOn': '/Date(1423681841700)/'},
            'DeliveryCity': 'Irvine',
            'DeliveryCountry': 'United State of Amercia',
            'DeliveryName': '17971 Sky Park Circle, Suite G',
            'DeliveryPostCode': '92614',
            'DeliveryRegion': 'CA',
            'DeliveryStreetAddress': '17971 Sky Park Circle, Suite G',
            'DeliveryStreetAddress2': None,
            'DeliverySuburb': None,
            'DiscountRate': 0.0,
            'ExchangeRate': 1.0,
            'Guid': 'a4cddceb-8f2c-4f83-bfcf-fecaa0229832'

                                    'LineTotal': 120.02,
                                    'OrderQuantity': 1050.0,
                                    'Product': {'Guid': 'aa887cd0-33f3-4883-927e-3c2ba5c8bfeb',
                                                'ProductCode': 'ISAAMDTRKT',
                                                'ProductDescription': 'Insert '
                                                                      'AnteAGE '
                                                                      'MD '
                                                                      'Travel '
                                                                      'Size '
                                                                      'Kit'},
                                    'ReceiptQuantity': None,
                                    'Tax': None,
                                    'UnitPrice': 0.1143,
                                    'Volume': None,
                 

            'Supplier': {'Guid': '946b53ce-5c74-465c-86d7-90ce6fea78ea',
                         'SupplierCode': 'Copy Group',
                         'SupplierName': 'Copy Group'},
            'SupplierInvoiceDate': '/Date(1447445017000)/',
            'SupplierRef': None,
            'Tax': {'CanApplyToExpenses': False,
                    'CanApplyToRevenue': False,
                    'Description': None,
                    'Guid': '00000000-0000-0000-0000-000000000000',
                    'LastModifiedOn': None,
                    'Obsolete': False,
                    'TaxCode': 'None',
                    'TaxRate': 0.0},
            'TaxRate': 0.0,
            'TaxTotal': 0.0,
            'Total': 104.16,
            'TotalVolume': 0.0,
            'TotalWeight': 0.0,
            'Warehouse': {'AddressLine1': '18218 E McDurmott, STE B',
                          'AddressLine2': None,
                          'City': 'Irvine',
                          'ContactName': 'Conn

                                    'Volume': None,
                                    'Weight': None}],
            'ReceivedDate': '/Date(1448415436759)/',
            'RequiredDate': '/Date(1448006400000)/',
            'SalesOrders': [],
            'SubTotal': 147.2,
            'Supplier': {'Guid': '8931af01-17c5-4eb9-8623-e83f8c8cebc7',
                         'SupplierCode': 'Bottles.com',
                         'SupplierName': 'Bottles.com'},
            'SupplierInvoiceDate': '/Date(1448404636000)/',
            'SupplierRef': None,
            'Tax': {'CanApplyToExpenses': False,
                    'CanApplyToRevenue': False,
                    'Description': None,
                    'Guid': '00000000-0000-0000-0000-000000000000',
                    'LastModifiedOn': None,
                    'Obsolete': False,
                    'TaxCode': 'None',
                    'TaxRate': 0.0},
            'TaxRate': 0.0,
            'TaxTotal': 0.0,
            'Total': 147.

...

                                    'BCUnitPrice': 0.518,
                                    'Comments': None,
                                    'DiscountRate': 0.0,
                                    'DiscountedUnitPrice': 0.518,
                                    'DueDate': '/Date(1515484800000)/',
                                    'Guid': '5046e262-b72f-48eb-8e48-f1415bfd34f9',
                                    'LastModifiedOn': '/Date(1519082641407)/',
                                    'LineNumber': 1,
                                    'LineTax': 0.0,
                                    'LineTotal': 1424.5,
                                    'OrderQuantity': 2750.0,
                                    'Product': {'Guid': 'c7bbfbbb-a190-4e72-81dc-7cbe9dd7d01c',
                                                'ProductCode': 'BXAAPRSE30ML',
                                                'ProductDescription': 'Box '
                                                       

                          'DDINumber': None,
                          'FaxNumber': None,
                          'Guid': '747d23bc-6283-448d-8568-e7bdf9399c64',
                          'IsDefault': True,
                          'LastModifiedOn': '/Date(1515700334676)/',
                          'MobileNumber': '949 510 4798',
                          'Obsolete': False,
                          'PhoneNumber': '949 510 4798',
                          'PostCode': '92614',
                          'Region': 'CA',
                          'StreetNo': '18218 E McDurmott, STE B',
                          'Suburb': None,
                          'WarehouseCode': 'SPW',
                          'WarehouseName': 'McDurmott Warehouse'},
            'XeroTaxCode': 'NoTax'},
           {'BCSubTotal': 0.0,
            'BCTaxTotal': 0.0,
            'BCTotal': 0.0,
            'Comments': 'Include Cost of Tooling',
            'CompletedDate': None,
            'CreatedBy': 'connor@ce

            'BCTaxTotal': 0.0,
            'BCTotal': 249.0,
            'Comments': None,
            'CompletedDate': '/Date(1521746935446)/',
            'CreatedBy': 'connor@cellese.com',
            'CreatedOn': '/Date(1521136985682)/',
            'Currency': {'CurrencyCode': 'USD',
                         'Description': 'United States of America, Dollars',
                         'Guid': 'e9718993-b8d1-4084-9476-5b0153413223',
                         'LastModifiedOn': '/Date(1423681841700)/'},
            'DeliveryCity': 'Irvine',
            'DeliveryCountry': 'United States of America',
            'DeliveryName': '18218 E McDurmott, STE B',
            'DeliveryPostCode': '92614',
            'DeliveryRegion': 'CA',
            'DeliveryStreetAddress': '18218 E McDurmott, STE B',
            'DeliveryStreetAddress2': None,
            'DeliverySuburb': None,
            'DiscountRate': 0.0,
            'ExchangeRate': 1.0,
            'Guid': '1a98c320-c9df-4fdb-9b86-1bd24

                          'Suburb': None,
                          'WarehouseCode': 'SPW',
                          'WarehouseName': 'McDurmott Warehouse'},
            'XeroTaxCode': 'NONE'},
           {'BCSubTotal': 0.0,
            'BCTaxTotal': 0.0,
            'BCTotal': 0.0,
            'Comments': 'VRS Tube Order',
            'CompletedDate': None,
            'CreatedBy': 'connor@cellese.com',
            'CreatedOn': '/Date(1521762036613)/',
            'Currency': {'CurrencyCode': 'USD',
                         'Description': 'United States of America, Dollars',
                         'Guid': 'e9718993-b8d1-4084-9476-5b0153413223',
                         'LastModifiedOn': '/Date(1423681841700)/'},
            'DeliveryCity': 'Irvine',
            'DeliveryCountry': 'United State of Amercia',
            'DeliveryName': '18218 E McDurmott, STE B',
            'DeliveryPostCode': '92614',
            'DeliveryRegion': 'CA',
            'DeliveryStreetAddress': '18218 E

                                    'Product': {'Guid': '3ca00d49-5658-424d-9d06-4e5bb7a0ae7a',
                                                'ProductCode': 'EBMN2ML',
                                                'ProductDescription': 'Bottle '
                                                                      'Microneedling '
                                                                      'Solution '
                                                                      'Roller '
                                                                      '2ml'},
                                    'ReceiptQuantity': None,
                                    'Tax': None,
                                    'UnitPrice': 0.23,
                                    'Volume': 0.0,
                                    'Weight': None}],
            'ReceivedDate': None,
            'RequiredDate': '/Date(1521529200000)/',
            'SalesOrders': [],
            'SubTotal': 20010.0,
  

In [85]:
len(purchase_orders["Items"])

158